In [60]:
import requests
import numpy as np
import pandas as pd
from requests_throttler import BaseThrottler
from shapely.geometry import Point, LineString, Polygon, MultiPolygon
import geopandas as gpd

import logging
logger = logging.getLogger()
logger.setLevel(logging.CRITICAL)

In [63]:
def get_poly(r):
    try:
        shapes = r['results'][0]['shapes']
        polys = []
        for shape in shapes:
            polys.append(Polygon(LineString([Point(p['lng'], p['lat']) for p in shape['shell']])))
        return MultiPolygon(polys)
    except:
        return Polygon()

In [2]:
app_id = '02974100'
key = 'ad6a6e483dfb044ec41c2ca39e5e681e'

endpoint = 'https://api.traveltimeapp.com/v4/time-map?'
params = 'type={_type}&travel_time={time}&lat={lat}&lng={lng}&departure_time={departure}&app_id={app_id}&api_key={key}'
lat, lng = 39.4681, -0.3808
_min, _max, step = 1, 30, 1
departure = '2023-06-15T12:00:00Z'

In [ ]:
data = []
for mode in ['cycling', 'driving', 'public_transport']:
    print(f'Requests for {mode}.')
    urls = [
        endpoint+params.format(
            _type=mode,
            time=time,
            lat=lat,
            lng=lng,
            departure=departure,
            app_id=app_id,
            key=key
        ) for time in range(60 * _min, 60*_max, 60*step)
    ]
    
    with BaseThrottler(name='base-throttler', delay=1/20) as bt:
        reqs = [requests.Request(method='GET', url=url) for url in urls]
        throttled_requests = bt.multi_submit(reqs)
        
    for i, r in enumerate([tr.response for tr in throttled_requests]):
        if r.status_code == 200:
            data.append({
                'mode': mode,
                '_range': (i+1 * step) * 60,
                'geom': get_poly(r.json()),
                'error': np.nan
            })
        else:
            data.append({
                'error': r.reason,
                'response': r.json()
            })

In [64]:
df = pd.DataFrame(data)
df['geom'] = df.response.apply(get_poly)
df_final = df.drop(columns=['response'])
df_final.head()

/Users/tomasehrenfeld/miniconda3/lib/python3.9/site-packages/pandas/core/dtypes/inference.py:383: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  iter(obj)  # Can iterate over it.
/Users/tomasehrenfeld/miniconda3/lib/python3.9/site-packages/pandas/core/dtypes/inference.py:384: ShapelyDeprecationWarning: __len__ for multi-part geometries is deprecated and will be removed in Shapely 2.0. Check the length of the `geoms` property instead to get the  number of parts of a multi-part geometry.
  len(obj)  # Has a length associated with it.
/Users/tomasehrenfeld/miniconda3/lib/python3.9/site-packages/pandas/io/formats/printing.py:117: ShapelyDeprecationWarning: Iteration over multi-part geometries is deprecated and will be removed in Shapely 2.0. Use the `geoms` property to access the constituent parts of a multi-part geometry.
  s = iter(seq)
/

mode  range  error                                               geom
0  cycling     60    NaN  (POLYGON ((-0.38057974 39.467888, -0.3799987 3...
1  cycling    120    NaN  (POLYGON ((-0.38347313 39.467453, -0.3828921 3...
2  cycling    180    NaN  (POLYGON ((-0.38462642 39.471066, -0.38520744 ...
3  cycling    240    NaN  (POLYGON ((-0.38635376 39.468834, -0.3857728 3...
4  cycling    300    NaN  (POLYGON ((-0.39041156 39.471096, -0.39041156 ...

In [77]:

df_final.rename(columns={'range':'_range'}).to_gbq(
    destination_table='accesibility.isolines',
    project_id='cartodb-gcp-solutions-eng-team',
    if_exists='replace',
    table_schema=[{'name': 'geom', 'type': 'GEOGRAPHY'}]
)

1it [00:05,  5.48s/it]


In [81]:
from google.cloud import bigquery
from datetime import datetime
client = bigquery.Client()

In [141]:
_ranges = client.query('''
  select 
    mode, 
    _range,
    st_union_agg(st_intersection(r.geom, st_boundary(i.geom))) as geom
  from `cartodb-gcp-solutions-eng-team.accesibility.valencia_roads` r
  join`cartodb-gcp-solutions-eng-team.accesibility.isolines` i
  on st_intersects(r.geom, i.geom)
  where not st_isempty(st_intersection(r.geom, st_boundary(i.geom)))
  group by mode, _range
''').to_geodataframe()

In [146]:
unary_points = []
for mode in _ranges['mode'].unique():
    for _range in sorted(_ranges[_ranges['mode']==mode]._range.unique()):
        unary_points.append({
            'mode': mode,
            '_range': _range,
            'geom': _ranges[(_ranges['mode']==mode ) & _ranges._range <= _range].unary_union
        })

In [150]:
pd.DataFrame(unary_points).loc[4, 'geom']

In [148]:
gdf = gpd.GeoDataFrame(pd.DataFrame(unary_points), geometry='geom', crs=4326)

KeyboardInterrupt: 